# QASPER evaluation

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import json
import os
import plotly.express as px
import plotly.graph_objects as go
import dataset_reader
from transformers.tokenization_utils_base import BatchEncoding
from datetime import date
from tqdm import tqdm

/Users/ag2435/anaconda3/envs/arxiv-agent/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
input_paths = {
    'train': 'original_data/qasper-train-dev-v0.3/qasper-train-v0.3.json',
    'dev': 'original_data/qasper-train-dev-v0.3/qasper-dev-v0.3.json',
    'test': 'original_data/qasper-test-and-evaluator-v0.3/qasper-test-v0.3.json',
}

In [4]:
output_path = 'data'
split = 'dev'
input_path = input_paths[split]
assert split in input_path

In [5]:
reader = dataset_reader.QasperReader(include_global_attention_mask=False)
instances = list(reader._read(input_path))

In [6]:
reader._stats

defaultdict(int,
            {'number of documents': 281,
             'number of questions': 1005,
             'number of answers': 1764,
             'questions with multiple answers': 744,
             'extractive questions': 962,
             'extractive questions with multiple spans': 406,
             'multiple_evidence_spans_count': 536,
             'answers with table or figure as evidence': 212,
             'freeform answers': 431,
             'yes/no questions': 208,
             'answers with no evidence': 212,
             'unanswerable questions': 163,
             'number of truncated contexts': 15})

In [7]:
# filter instances that have valid html
from arxiv_agent.tools.paper.utils import get_soup
from functools import cache
from time import sleep

@cache
def has_html(arxiv_id):
    sleep(0.1)
    try:
        ERROR_MSG = "Conversion to HTML had a Fatal error and exited abruptly. This document may be truncated or damaged."
        soup = get_soup(arxiv_id)
        return ERROR_MSG not in soup.text
    except Exception as e:
        return False

In [8]:
has_html(instances[0]['metadata']['article_id'])

True

In [9]:
has_html("2003.03106")

False

In [10]:
# plot histogram of full_text lengths
question_token_lengths = []
for inst in instances:
    question_token_lengths.append(len(inst['question_with_context']))
    
px.histogram(question_token_lengths, 
             title=f'Histogram of question + context token lengths (total={len(question_token_lengths)})')

In [11]:
# arxiv id to year
def article_id_to_date(article_id):
    year = article_id[:2]
    month = article_id[2:4]
    dt = date(int('20' + year), int(month), 1)
    return dt

In [12]:
article_id_to_date('2001.0001')

datetime.date(2020, 1, 1)

In [13]:
# get year distribution
years = []
for inst in instances:
    dt = article_id_to_date(inst['metadata']['article_id'])
    # print(dt)
    years.append(dt)

In [14]:
px.histogram(years,)

## Save instances to JSON

In [15]:
# recursively check the type of each field in the dataset
def check_type(data, level=0):
    tabs = '\t' * level
    if isinstance(data, dict):
        for key, value in data.items():
            print(f'{tabs}{key}: {type(value)}')
            check_type(value, level + 1)
    elif isinstance(data, list):
        for i in data:
            check_type(i, level + 1)
    else:
        pass
        # print(f'{tabs}{type(data)}')
        # if isinstance(data, BatchEncoding):
        #     print(f'{tabs}{data[:100]}')

In [16]:
check_type(instances[0])

question_with_context: <class 'list'>
paragraph_indices: <class 'list'>
evidence: <class 'list'>
answer: <class 'list'>
metadata: <class 'dict'>
	question: <class 'str'>
	question_tokens: <class 'list'>
	paragraphs: <class 'list'>
	context_tokens: <class 'list'>
	question_id: <class 'str'>
	article_id: <class 'str'>
	all_answers: <class 'list'>
			text: <class 'str'>
			type: <class 'str'>
			text: <class 'str'>
			type: <class 'str'>
	all_evidence: <class 'list'>
	all_evidence_masks: <class 'list'>


In [17]:
# save instances to file
with open(os.path.join(output_path, f'{split}_instances_with_html.json'), 'w') as f:
    # pretty print json
    instances_with_html = [inst for inst in tqdm(instances) if has_html(inst['metadata']['article_id'])]
    print(f'Number of instances: {len(instances)}')
    print(f'Number of instances with html: {len(instances_with_html)}')
    json.dump(instances_with_html, f, indent=4)

  0%|          | 0/1005 [00:00<?, ?it/s]huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
100%|██████████| 1005/1005 [01:27<00:00, 11.45it/s]


Number of instances: 1005
Number of instances with html: 978
